In [0]:
#load data from fact table
df = spark.table("goldwind.fact")


+-------------+----------+--------+----------+---------+----------+--------------+---------------+
|production_id|   date_id| time_id|turbine_id|status_id|wind_speed|wind_direction|energy_produced|
+-------------+----------+--------+----------+---------+----------+--------------+---------------+
|            1|2024-06-01|00-00-00|         1|        4|  18.44936|            SE|     1786.91843|
|            2|2024-06-01|00-00-00|         2|        4|  16.34197|             E|     1156.38082|
|            3|2024-06-01|00-00-00|         3|        4|  24.16424|             E|     1216.49768|
|            4|2024-06-01|00-10-00|         1|        4|  13.03947|            NE|     1888.39496|
|            5|2024-06-01|00-10-00|         2|        4|   4.00397|            SE|     1052.36231|
|            6|2024-06-01|00-10-00|         3|        6|   5.22807|             N|            0.0|
|            7|2024-06-01|00-20-00|         1|        6|  20.38065|            SE|            0.0|
|         

In [0]:

# 📘 Notebook ML - Prédiction de l'énergie produite par les turbines (version enrichie avec toutes les dimensions)

# 1. Chargement des données GOLD et dimensions
fact = spark.table("goldwind.fact")
dim_turbine = spark.table("goldwind.dim_turbine")
dim_date = spark.table("goldwind.dim_date")
dim_time = spark.table("goldwind.dim_time")
dim_status = spark.table("goldwind.dim_status")

# 2. Jointures pour enrichir les données
fact_joined = fact \
    .join(dim_turbine, "turbine_id", "left") \
    .join(dim_date, fact.date_id == dim_date.date_id, "left") \
    .join(dim_time, fact.time_id == dim_time.time_id, "left") \
    .join(dim_status, "status_id", "left")

# 3. Ajout de la colonne saison (facultatif mais utile) je devais normalement le mettre dans mon fichier silver lol
from pyspark.sql.functions import when, col

fact_joined = fact_joined.withColumn(
    "season",
    when(col("month").isin(12, 1, 2), "winter")
    .when(col("month").isin(3, 4, 5), "spring")
    .when(col("month").isin(6, 7, 8), "summer")
    .when(col("month").isin(9, 10, 11), "autumn")
)

# 4. Nettoyage et filtrage des données
fact_filtered = fact_joined.filter(col("energy_produced") > 0).dropna(subset=[
    "wind_speed", "wind_direction", "turbine_id", "status_id", "energy_produced",
    "hour", "month", "capacity", "responsible_department"
])
display(fact_filtered)

status_id turbine_id production_id date_id time_id wind_speed wind_direction energy_produced turbine_name capacity latitude longitude region date_id year month day quarter time_id hour minute second status responsible_department season 4 1 1 2024-06-01 00-00-00 18.44936 SE 1786.91843 Turbine A 2200 34.0 -118.0 Region A 2024-06-01 2024 6 1 2 00-00-00 00 00 00 Online Operations summer 4 1 4 2024-06-01 00-10-00 13.03947 NE 1888.39496 Turbine A 2200 34.0 -118.0 Region A 2024-06-01 2024 6 1 2 00-10-00 00 10 00 Online Operations summer 4 1 10 2024-06-01 00-30-00 6.28564 E 1184.2255 Turbine A 2200 34.0 -118.0 Region A 2024-06-01 2024 6 1 2 00-30-00 00 30 00 Online Operations summer 4 1 13 2024-06-01 00-40-00 12.05173 NE 648.92053 Turbine A 2200 34.0 -118.0 Region A 2024-06-01 2024 6 1 2 00-40-00 00 40 00 Online Operations summer 4 1 16 2024-06-01 00-50-00 2.88378 SE 1982.56076 Turbine A 2200 34.0 -118.0 Region A 2024-06-01 2024 6 1 2 00-50-00 00 50 00 Online Operations summer 4 1 19 2024-06-01 01-00-00 4.53863 SW 975.80261 Turbine A 2200 34.0 -118.0 Region A 2024-06-01 2024 6 1 2 01-00-00 01 00 00 Online Operations summer 4 1 22 2024-06-01 01-10-00 13.72136 N 1407.26828 Turbine A 2200 34.0 -118.0 Region A 2024-06-01 2024 6 1 2 01-10-00 01 10 00 Online Operations summer 4 1 25 2024-06-01 01-20-00 3.47539 E 1347.7833 Turbine A 2200 34.0 -118.0 Region A 2024-06-01 2024 6 1 2 01-20-00 01 20 00 Online Operations summer 4 1 28 2024-06-01 01-30-00 16.88501 W 934.10914 Turbine A 2200 34.0 -118.0 Region A 2024-06-01 2024 6 1 2 01-30-00 01 30 00 Online Operations summer 4 1 31 2024-06-01 01-40-00 24.13034 N 1634.16004 Turbine A 2200 34.0 -118.0 Region A 2024-06-01 2024 6 1 2 01-40-00 01 40 00 Online Operations summer 4 1 37 2024-06-01 02-00-00 23.98992 NE 1092.30394 Turbine A 2200 34.0 -118.0 Region A 2024-06-01 2024 6 1 2 02-00-00 02 00 00 Online Operations summer 4 1 40 2024-06-01 02-10-00 4.36586 W 1354.94737 Turbine A 2200 34.0 -118.0 Region A 2024-06-01 2024 6 1 2 02-10-00 02 10 00 Online Operations summer 4 1 43 2024-06-01 02-20-00 22.51424 SW 1305.53378 Turbine A 2200 34.0 -118.0 Region A 2024-06-01 2024 6 1 2 02-20-00 02 20 00 Online Operations summer 4 1 46 2024-06-01 02-30-00 13.69126 NE 685.72997 Turbine A 2200 34.0 -118.0 Region A 2024-06-01 2024 6 1 2 02-30-00 02 30 00 Online Operations summer 4 1 49 2024-06-01 02-40-00 21.92679 NW 524.94196 Turbine A 2200 34.0 -118.0 Region A 2024-06-01 2024 6 1 2 02-40-00 02 40 00 Online Operations summer 4 1 52 2024-06-01 02-50-00 5.93269 E 835.88703 Turbine A 2200 34.0 -118.0 Region A 2024-06-01 2024 6 1 2 02-50-00 02 50 00 Online Operations summer 4 1 55 2024-06-01 03-00-00 23.48692 NW 1518.63592 Turbine A 2200 34.0 -118.0 Region A 2024-06-01 2024 6 1 2 03-00-00 03 00 00 Online Operations summer 4 1 58 2024-06-01 03-10-00 12.39851 NW 841.12194 Turbine A 2200 34.0 -118.0 Region A 2024-06-01 2024 6 1 2 03-10-00 03 10 00 Online Operations summer 4 1 61 2024-06-01 03-20-00 3.54674 NE 1217.89449 Turbine A 2200 34.0 -118.0 Region A 2024-06-01 2024 6 1 2 03-20-00 03 20 00 Online Operations summer 4 1 64 2024-06-01 03-30-00 22.27646 SE 1075.19584 Turbine A 2200 34.0 -118.0 Region A 2024-06-01 2024 6 1 2 03-30-00 03 30 00 Online Operations summer 4 1 70 2024-06-01 03-50-00 18.80017 SW 1195.36314 Turbine A 2200 34.0 -118.0 Region A 2024-06-01 2024 6 1 2 03-50-00 03 50 00 Online Operations summer 4 1 73 2024-06-01 04-00-00 15.00469 SW 807.29864 Turbine A 2200 34.0 -118.0 Region A 2024-06-01 2024 6 1 2 04-00-00 04 00 00 Online Operations summer 4 1 76 2024-06-01 04-10-00 18.82896 E 1942.90457 Turbine A 2200 34.0 -118.0 Region A 2024-06-01 2024 6 1 2 04-10-00 04 10 00 Online Operations summer 4 1 79 2024-06-01 04-20-00 15.48743 NW 1268.59019 Turbine A 2200 34.0 -118.0 Region A 2024-06-01 2024 6 1 2 04-20-00 04 20 00 Online Operations summer 4 1 82 2024-06-01 04-30-00 18.45791 S 1445.67191 Turbine A 2200 34.0 -118.0 Region A 2024-06-01 2024 6 1 2 04-30-00 04 30 00 Online Operations summer 4 1 91 2024-06-01

In [0]:
# 4. Nettoyage et filtrage des données
fact_filtered = fact_joined.filter(col("energy_produced") > 0).dropna(subset=[
    "wind_speed", "wind_direction", "turbine_id", "status_id", "energy_produced",
    "hour", "month", "capacity", "responsible_department"
])

# 5. Encodages nécessaires
from pyspark.ml.feature import StringIndexer, VectorAssembler

indexer_dir = StringIndexer(inputCol="wind_direction", outputCol="wind_dir_indexed")
indexer_dept = StringIndexer(inputCol="responsible_department", outputCol="responsible_dept_indexed")
indexer_season = StringIndexer(inputCol="season", outputCol="season_indexed")

indexed = indexer_dir.fit(fact_filtered).transform(fact_filtered)
indexed = indexer_dept.fit(indexed).transform(indexed)
indexed = indexer_season.fit(indexed).transform(indexed)

# 🔧 Conversion de types pour VectorAssembler
indexed = indexed.withColumn("hour", col("hour").cast("int"))
indexed = indexed.withColumn("month", col("month").cast("int"))
indexed = indexed.withColumn("capacity", col("capacity").cast("int"))

# 6. Assemblage des features enrichies
assembler = VectorAssembler(
    inputCols=[
        "wind_speed",
        "wind_dir_indexed",
        "turbine_id",
        "status_id",
        "hour",
        "month",
        "capacity",
        "responsible_dept_indexed",
        "season_indexed"
    ],
    outputCol="features"
)
final_data = assembler.transform(indexed).select("features", "energy_produced")
display(final_data)

features energy_produced Map(vectorType -> dense, length -> 9, values -> List(18.44936, 3.0, 1.0, 4.0, 0.0, 6.0, 2200.0, 0.0, 0.0)) 1786.91843 Map(vectorType -> dense, length -> 9, values -> List(13.03947, 1.0, 1.0, 4.0, 0.0, 6.0, 2200.0, 0.0, 0.0)) 1888.39496 Map(vectorType -> dense, length -> 9, values -> List(6.28564, 6.0, 1.0, 4.0, 0.0, 6.0, 2200.0, 0.0, 0.0)) 1184.2255 Map(vectorType -> dense, length -> 9, values -> List(12.05173, 1.0, 1.0, 4.0, 0.0, 6.0, 2200.0, 0.0, 0.0)) 648.92053 Map(vectorType -> dense, length -> 9, values -> List(2.88378, 3.0, 1.0, 4.0, 0.0, 6.0, 2200.0, 0.0, 0.0)) 1982.56076 Map(vectorType -> dense, length -> 9, values -> List(4.53863, 0.0, 1.0, 4.0, 1.0, 6.0, 2200.0, 0.0, 0.0)) 975.80261 Map(vectorType -> dense, length -> 9, values -> List(13.72136, 4.0, 1.0, 4.0, 1.0, 6.0, 2200.0, 0.0, 0.0)) 1407.26828 Map(vectorType -> dense, length -> 9, values -> List(3.47539, 6.0, 1.0, 4.0, 1.0, 6.0, 2200.0, 0.0, 0.0)) 1347.7833 Map(vectorType -> dense, length -> 9, values -> List(16.88501, 7.0, 1.0, 4.0, 1.0, 6.0, 2200.0, 0.0, 0.0)) 934.10914 Map(vectorType -> dense, length -> 9, values -> List(24.13034, 4.0, 1.0, 4.0, 1.0, 6.0, 2200.0, 0.0, 0.0)) 1634.16004 Map(vectorType -> dense, length -> 9, values -> List(23.98992, 1.0, 1.0, 4.0, 2.0, 6.0, 2200.0, 0.0, 0.0)) 1092.30394 Map(vectorType -> dense, length -> 9, values -> List(4.36586, 7.0, 1.0, 4.0, 2.0, 6.0, 2200.0, 0.0, 0.0)) 1354.94737 Map(vectorType -> dense, length -> 9, values -> List(22.51424, 0.0, 1.0, 4.0, 2.0, 6.0, 2200.0, 0.0, 0.0)) 1305.53378 Map(vectorType -> dense, length -> 9, values -> List(13.69126, 1.0, 1.0, 4.0, 2.0, 6.0, 2200.0, 0.0, 0.0)) 685.72997 Map(vectorType -> dense, length -> 9, values -> List(21.92679, 5.0, 1.0, 4.0, 2.0, 6.0, 2200.0, 0.0, 0.0)) 524.94196 Map(vectorType -> dense, length -> 9, values -> List(5.93269, 6.0, 1.0, 4.0, 2.0, 6.0, 2200.0, 0.0, 0.0)) 835.88703 Map(vectorType -> dense, length -> 9, values -> List(23.48692, 5.0, 1.0, 4.0, 3.0, 6.0, 2200.0, 0.0, 0.0)) 1518.63592 Map(vectorType -> dense, length -> 9, values -> List(12.39851, 5.0, 1.0, 4.0, 3.0, 6.0, 2200.0, 0.0, 0.0)) 841.12194 Map(vectorType -> dense, length -> 9, values -> List(3.54674, 1.0, 1.0, 4.0, 3.0, 6.0, 2200.0, 0.0, 0.0)) 1217.89449 Map(vectorType -> dense, length -> 9, values -> List(22.27646, 3.0, 1.0, 4.0, 3.0, 6.0, 2200.0, 0.0, 0.0)) 1075.19584 Map(vectorType -> dense, length -> 9, values -> List(18.80017, 0.0, 1.0, 4.0, 3.0, 6.0, 2200.0, 0.0, 0.0)) 1195.36314 Map(vectorType -> dense, length -> 9, values -> List(15.00469, 0.0, 1.0, 4.0, 4.0, 6.0, 2200.0, 0.0, 0.0)) 807.29864 Map(vectorType -> dense, length -> 9, values -> List(18.82896, 6.0, 1.0, 4.0, 4.0, 6.0, 2200.0, 0.0, 0.0)) 1942.90457 Map(vectorType -> dense, length -> 9, values -> List(15.48743, 5.0, 1.0, 4.0, 4.0, 6.0, 2200.0, 0.0, 0.0)) 1268.59019 Map(vectorType -> dense, length -> 9, values -> List(18.45791, 2.0, 1.0, 4.0, 4.0, 6.0, 2200.0, 0.0, 0.0)) 1445.67191 Map(vectorType -> dense, length -> 9, values -> List(7.34139, 3.0, 1.0, 4.0, 5.0, 6.0, 2200.0, 0.0, 0.0)) 987.96546 Map(vectorType -> dense, length -> 9, values -> List(20.63975, 2.0, 1.0, 4.0, 5.0, 6.0, 2200.0, 0.0, 0.0)) 1130.8092 Map(vectorType -> dense, length -> 9, values -> List(12.49123, 5.0, 1.0, 4.0, 5.0, 6.0, 2200.0, 0.0, 0.0)) 1163.02298 Map(vectorType -> dense, length -> 9, values -> List(17.67126, 7.0, 1.0, 4.0, 5.0, 6.0, 2200.0, 0.0, 0.0)) 1060.71971 Map(vectorType -> dense, length -> 9, values -> List(13.93321, 3.0, 1.0, 4.0, 5.0, 6.0, 2200.0, 0.0, 0.0)) 1232.61509 Map(vectorType -> dense, length -> 9, values -> List(14.40214, 0.0, 1.0, 4.0, 5.0, 6.0, 2200.0, 0.0, 0.0)) 1089.01351 Map(vectorType -> dense, length -> 9, values -> List(18.65586, 6.0, 1.0, 4.0, 6.0, 6.0, 2200.0, 0.0, 0.0)) 640.18918 Map(vectorType -> dense, length -> 9, values -> List(9.09058, 7.0, 1.0, 4.0, 6.0, 6.0, 2200.0, 0.0, 0.0)) 1187.20824 Map(vectorType -> dense, length -> 9, values -> List(5.66653, 7.0, 1.0, 4.0, 6.0, 6.0, 2200.0, 0.0, 0.0

In [0]:
# 7. Split en train/test
train_data, test_data = final_data.randomSplit([0.8, 0.2], seed=42)


In [0]:

# 8. Entraînement et comparaison de plusieurs modèles
from pyspark.ml.regression import LinearRegression, DecisionTreeRegressor, RandomForestRegressor
from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.ml import Pipeline
import mlflow
import mlflow.spark

models = {
    "LinearRegression": LinearRegression(labelCol="energy_produced", featuresCol="features"),
    "DecisionTree": DecisionTreeRegressor(labelCol="energy_produced", featuresCol="features"),
    "RandomForest": RandomForestRegressor(labelCol="energy_produced", featuresCol="features")
}

results = []

for name, algo in models.items():
    with mlflow.start_run(run_name=name):
        pipeline = Pipeline(stages=[algo])
        model = pipeline.fit(train_data)
        predictions = model.transform(test_data)

        evaluator = RegressionEvaluator(labelCol="energy_produced", predictionCol="prediction", metricName="rmse")
        rmse = evaluator.evaluate(predictions)

        mlflow.spark.log_model(model, f"model_{name}")
        mlflow.log_metric("rmse", rmse)

        results.append((name, rmse))
        print(f"📊 {name} RMSE: {rmse:.4f}")

# 9. Sélection du meilleur modèle
best_model_name, best_rmse = sorted(results, key=lambda x: x[1])[0]
print(f"\n✅ Meilleur modèle : {best_model_name} avec RMSE = {best_rmse:.4f}")

2025/04/22 12:26:53 INFO mlflow.spark: Inferring pip requirements by reloading the logged model from the databricks artifact repository, which can be time-consuming. To speed up, explicitly specify the conda_env or pip_requirements when calling log_model().
2025/04/22 12:27:25 WARNING mlflow.utils.environment: Encountered an unexpected error while inferring pip requirements (model URI: dbfs:/databricks/mlflow-tracking/7146a1d339d64ccfa347b14638dcb1e3/41f7bf8ff25643ad9cb6e78f3fb0ca1b/artifacts/model_LinearRegression/sparkml, flavor: spark). Fall back to return ['pyspark==3.5.0']. Set logging level to DEBUG to see the full traceback. 


📊 LinearRegression RMSE: 430.6956


2025/04/22 12:27:36 INFO mlflow.spark: Inferring pip requirements by reloading the logged model from the databricks artifact repository, which can be time-consuming. To speed up, explicitly specify the conda_env or pip_requirements when calling log_model().
2025/04/22 12:28:08 WARNING mlflow.utils.environment: Encountered an unexpected error while inferring pip requirements (model URI: dbfs:/databricks/mlflow-tracking/7146a1d339d64ccfa347b14638dcb1e3/341bbbccd4e54259a7d63731ef9d72a4/artifacts/model_DecisionTree/sparkml, flavor: spark). Fall back to return ['pyspark==3.5.0']. Set logging level to DEBUG to see the full traceback. 


📊 DecisionTree RMSE: 437.4546


2025/04/22 12:28:24 INFO mlflow.spark: Inferring pip requirements by reloading the logged model from the databricks artifact repository, which can be time-consuming. To speed up, explicitly specify the conda_env or pip_requirements when calling log_model().
2025/04/22 12:28:56 WARNING mlflow.utils.environment: Encountered an unexpected error while inferring pip requirements (model URI: dbfs:/databricks/mlflow-tracking/7146a1d339d64ccfa347b14638dcb1e3/f825afa308e74e97ac45cf50ad4f50c7/artifacts/model_RandomForest/sparkml, flavor: spark). Fall back to return ['pyspark==3.5.0']. Set logging level to DEBUG to see the full traceback. 


📊 RandomForest RMSE: 431.5084

✅ Meilleur modèle : LinearRegression avec RMSE = 430.6956


In [0]:
from pyspark.ml.regression import LinearRegression, DecisionTreeRegressor, RandomForestRegressor
from pyspark.ml.evaluation import RegressionEvaluator
from pyspark.ml import Pipeline
models = {
    "LinearRegression": LinearRegression(labelCol="energy_produced", featuresCol="features"),
    "DecisionTree": DecisionTreeRegressor(labelCol="energy_produced", featuresCol="features"),
    "RandomForest": RandomForestRegressor(labelCol="energy_produced", featuresCol="features")
}

results = []

for name, algo in models.items():
    pipeline = Pipeline(stages=[algo])
    model = pipeline.fit(train_data)
    predictions = model.transform(test_data)
    
    evaluator = RegressionEvaluator(labelCol="energy_produced", predictionCol="prediction", metricName="rmse")
    rmse = evaluator.evaluate(predictions)
    
    results.append((name, rmse))
    print(f"📊 {name} RMSE: {rmse:.4f}")
best_model_name, best_rmse = sorted(results, key=lambda x: x[1])[0]
print(f"\n✅ Meilleur modèle : {best_model_name} avec RMSE = {best_rmse:.4f}")


📊 LinearRegression RMSE: 430.8846
📊 DecisionTree RMSE: 426.2068
📊 RandomForest RMSE: 428.5398

✅ Meilleur modèle : DecisionTree avec RMSE = 426.2068


In [0]:

# 10. Réentraînement du meilleur modèle sur toutes les données
best_algo = models[best_model_name]
best_pipeline = Pipeline(stages=[best_algo])
best_model = best_pipeline.fit(final_data)

# 11. Prédictions complètes (batch)
full_predictions = best_model.transform(final_data)

# 12. Sauvegarde des prédictions en Delta table
full_predictions.select("features", "prediction").write.format("delta").mode("overwrite").saveAsTable("goldwind.predictions")

In [0]:
%sql
select  * from goldwind.predictions

features prediction Map(vectorType -> dense, length -> 9, values -> List(18.44936, 3.0, 1.0, 4.0, 0.0, 6.0, 2200.0, 0.0, 0.0)) 1277.2685464523315 Map(vectorType -> dense, length -> 9, values -> List(13.03947, 1.0, 1.0, 4.0, 0.0, 6.0, 2200.0, 0.0, 0.0)) 1287.5236234046488 Map(vectorType -> dense, length -> 9, values -> List(6.28564, 6.0, 1.0, 4.0, 0.0, 6.0, 2200.0, 0.0, 0.0)) 1271.95273040984 Map(vectorType -> dense, length -> 9, values -> List(12.05173, 1.0, 1.0, 4.0, 0.0, 6.0, 2200.0, 0.0, 0.0)) 1288.0139630972706 Map(vectorType -> dense, length -> 9, values -> List(2.88378, 3.0, 1.0, 4.0, 0.0, 6.0, 2200.0, 0.0, 0.0)) 1284.9957031055785 Map(vectorType -> dense, length -> 9, values -> List(4.53863, 0.0, 1.0, 4.0, 1.0, 6.0, 2200.0, 0.0, 0.0)) 1294.876657785981 Map(vectorType -> dense, length -> 9, values -> List(13.72136, 4.0, 1.0, 4.0, 1.0, 6.0, 2200.0, 0.0, 0.0)) 1275.179177858108 Map(vectorType -> dense, length -> 9, values -> List(3.47539, 6.0, 1.0, 4.0, 1.0, 6.0, 2200.0, 0.0, 0.0)) 1272.6960748869276 Map(vectorType -> dense, length -> 9, values -> List(16.88501, 7.0, 1.0, 4.0, 1.0, 6.0, 2200.0, 0.0, 0.0)) 1262.2544587697753 Map(vectorType -> dense, length -> 9, values -> List(24.13034, 4.0, 1.0, 4.0, 1.0, 6.0, 2200.0, 0.0, 0.0)) 1270.011890865878 Map(vectorType -> dense, length -> 9, values -> List(23.98992, 1.0, 1.0, 4.0, 2.0, 6.0, 2200.0, 0.0, 0.0)) 1280.7840640248 Map(vectorType -> dense, length -> 9, values -> List(4.36586, 7.0, 1.0, 4.0, 2.0, 6.0, 2200.0, 0.0, 0.0)) 1267.8175524133387 Map(vectorType -> dense, length -> 9, values -> List(22.51424, 0.0, 1.0, 4.0, 2.0, 6.0, 2200.0, 0.0, 0.0)) 1285.3013635491589 Map(vectorType -> dense, length -> 9, values -> List(13.69126, 1.0, 1.0, 4.0, 2.0, 6.0, 2200.0, 0.0, 0.0)) 1285.8965853146285 Map(vectorType -> dense, length -> 9, values -> List(21.92679, 5.0, 1.0, 4.0, 2.0, 6.0, 2200.0, 0.0, 0.0)) 1266.6693199744518 Map(vectorType -> dense, length -> 9, values -> List(5.93269, 6.0, 1.0, 4.0, 2.0, 6.0, 2200.0, 0.0, 0.0)) 1270.8244712522962 Map(vectorType -> dense, length -> 9, values -> List(23.48692, 5.0, 1.0, 4.0, 3.0, 6.0, 2200.0, 0.0, 0.0)) 1265.243094741049 Map(vectorType -> dense, length -> 9, values -> List(12.39851, 5.0, 1.0, 4.0, 3.0, 6.0, 2200.0, 0.0, 0.0)) 1270.7476683647387 Map(vectorType -> dense, length -> 9, values -> List(3.54674, 1.0, 1.0, 4.0, 3.0, 6.0, 2200.0, 0.0, 0.0)) 1290.2808511854073 Map(vectorType -> dense, length -> 9, values -> List(22.27646, 3.0, 1.0, 4.0, 3.0, 6.0, 2200.0, 0.0, 0.0)) 1273.4134659860079 Map(vectorType -> dense, length -> 9, values -> List(18.80017, 0.0, 1.0, 4.0, 3.0, 6.0, 2200.0, 0.0, 0.0)) 1286.493387659536 Map(vectorType -> dense, length -> 9, values -> List(15.00469, 0.0, 1.0, 4.0, 4.0, 6.0, 2200.0, 0.0, 0.0)) 1287.7258258003021 Map(vectorType -> dense, length -> 9, values -> List(18.82896, 6.0, 1.0, 4.0, 4.0, 6.0, 2200.0, 0.0, 0.0)) 1263.118956478622 Map(vectorType -> dense, length -> 9, values -> List(15.48743, 5.0, 1.0, 4.0, 4.0, 6.0, 2200.0, 0.0, 0.0)) 1268.5625122196757 Map(vectorType -> dense, length -> 9, values -> List(18.45791, 2.0, 1.0, 4.0, 4.0, 6.0, 2200.0, 0.0, 0.0)) 1278.4420904625415 Map(vectorType -> dense, length -> 9, values -> List(7.34139, 3.0, 1.0, 4.0, 5.0, 6.0, 2200.0, 0.0, 0.0)) 1279.5241484918295 Map(vectorType -> dense, length -> 9, values -> List(20.63975, 2.0, 1.0, 4.0, 5.0, 6.0, 2200.0, 0.0, 0.0)) 1276.7072322991169 Map(vectorType -> dense, length -> 9, values -> List(12.49123, 5.0, 1.0, 4.0, 5.0, 6.0, 2200.0, 0.0, 0.0)) 1269.398167088003 Map(vectorType -> dense, length -> 9, values -> List(17.67126, 7.0, 1.0, 4.0, 5.0, 6.0, 2200.0, 0.0, 0.0)) 1259.2571985870457 Map(vectorType -> dense, length -> 9, values -> List(13.93321, 3.0, 1.0, 4.0, 5.0, 6.0, 2200.0, 0.0, 0.0)) 1276.2517984881672 Map(vectorType -> dense, length -> 9, values -> List(14.40214, 0.0, 1.0, 4.0, 5.0, 6.0, 2200.0, 0.0, 0.0)) 1287.3732108757247 Map(vectorType -> dense, length -> 9, values -> List(18.65586, 6.0, 1.0, 4.0, 6.0, 6.0, 2200.0

In [0]:
#vue lisble 
# 13. Vue lisible des prédictions
from pyspark.ml.linalg import Vectors, VectorUDT
from pyspark.sql.functions import udf
from pyspark.sql.types import ArrayType, DoubleType

def extract_features(vector):
    return vector.toArray().tolist()

extract_udf = udf(extract_features, ArrayType(DoubleType()))

df = full_predictions.withColumn("features_array", extract_udf("features"))
df_lisible = df.selectExpr(
    "features_array[0] as wind_speed",
    "features_array[1] as wind_dir_indexed",
    "features_array[2] as turbine_id",
    "features_array[3] as status_id",
    "features_array[4] as hour",
    "features_array[5] as month",
    "features_array[6] as capacity",
    "features_array[7] as responsible_dept_indexed",
    "features_array[8] as season_indexed",
    "prediction"
)

# Affichage des prédictions lisibles
df_lisible.show()


+----------+----------------+----------+---------+----+-----+--------+------------------------+--------------+------------------+
|wind_speed|wind_dir_indexed|turbine_id|status_id|hour|month|capacity|responsible_dept_indexed|season_indexed|        prediction|
+----------+----------------+----------+---------+----+-----+--------+------------------------+--------------+------------------+
|  18.44936|             3.0|       1.0|      4.0| 0.0|  6.0|  2200.0|                     0.0|           0.0|1277.2685464523315|
|  13.03947|             1.0|       1.0|      4.0| 0.0|  6.0|  2200.0|                     0.0|           0.0|1287.5236234046488|
|   6.28564|             6.0|       1.0|      4.0| 0.0|  6.0|  2200.0|                     0.0|           0.0|  1271.95273040984|
|  12.05173|             1.0|       1.0|      4.0| 0.0|  6.0|  2200.0|                     0.0|           0.0|1288.0139630972706|
|   2.88378|             3.0|       1.0|      4.0| 0.0|  6.0|  2200.0|                    